In [186]:
# Exercise 1: train a trigram language model, i.e. 
# take two characters as an input to predict the 3rd one. 
# Feel free to use either counting or a neural net. 
# Evaluate the loss; Did it improve over a bigram model?

import torch
from itertools import product

In [187]:
words = open('names.txt', 'r').read().splitlines()

In [203]:
chars = set(''.join(words))
chars.add('.')
chars = sorted(chars)
combs = sorted([''.join(comb) for comb in product(chars, repeat=2)])

stoi = {s:i for i,s in enumerate(chars)}
ctoi = {c:i for i,c in enumerate(combs)}

itos = {s:i for i,s in stoi.items()}
itoc = {c:i for i,c in ctoi.items()}

In [204]:
xs, ys = [], []

for w in words:
    end = len(w) - 1
    combs = ['..'] + ['.' + w[0]] + [w[i] + w[i+1] for i in range(end)] + [w[end] + '.']
    print(combs)

    for comb, ch in zip(combs, combs[1:]):
        print(comb, ch[1])
        row = ctoi[comb]
        col = stoi[ch[1]]
        xs.append(row)
        ys.append(col)

xs = torch.tensor(xs)
ys = torch.tensor(ys)
num = xs.nelement()

print(xs)
print(ys)

g = torch.Generator().manual_seed(2147483647)
W = torch.randn((729, 27), generator=g, requires_grad=True)

['..', '.e', 'em', 'mm', 'ma', 'a.']
.. e
.e m
em m
mm a
ma .
['..', '.o', 'ol', 'li', 'iv', 'vi', 'ia', 'a.']
.. o
.o l
ol i
li v
iv i
vi a
ia .
['..', '.a', 'av', 'va', 'a.']
.. a
.a v
av a
va .
['..', '.i', 'is', 'sa', 'ab', 'be', 'el', 'll', 'la', 'a.']
.. i
.i s
is a
sa b
ab e
be l
el l
ll a
la .
['..', '.s', 'so', 'op', 'ph', 'hi', 'ia', 'a.']
.. s
.s o
so p
op h
ph i
hi a
ia .
['..', '.c', 'ch', 'ha', 'ar', 'rl', 'lo', 'ot', 'tt', 'te', 'e.']
.. c
.c h
ch a
ha r
ar l
rl o
lo t
ot t
tt e
te .
['..', '.m', 'mi', 'ia', 'a.']
.. m
.m i
mi a
ia .
['..', '.a', 'am', 'me', 'el', 'li', 'ia', 'a.']
.. a
.a m
am e
me l
el i
li a
ia .
['..', '.h', 'ha', 'ar', 'rp', 'pe', 'er', 'r.']
.. h
.h a
ha r
ar p
rp e
pe r
er .
['..', '.e', 'ev', 've', 'el', 'ly', 'yn', 'n.']
.. e
.e v
ev e
ve l
el y
ly n
yn .
['..', '.a', 'ab', 'bi', 'ig', 'ga', 'ai', 'il', 'l.']
.. a
.a b
ab i
bi g
ig a
ga i
ai l
il .
['..', '.e', 'em', 'mi', 'il', 'ly', 'y.']
.. e
.e m
em i
mi l
il y
ly .
['..', '.e', 'el', 'li', 

In [205]:
import torch.nn.functional as F
xenc = F.one_hot(xs, num_classes=729).float()
xenc.shape

torch.Size([228146, 729])

In [214]:
for k in range(100):
    xenc = F.one_hot(xs, num_classes=729).float()
    logits = xenc @ W
    counts = logits.exp()
    probs = counts / counts.sum(dim=1, keepdim=True)
    loss = -probs[torch.arange(num), ys].log().mean()
    print(loss.item())
    
    W.grad = None
    loss.backward()
    W.data += -50 * W.grad


2.381121873855591
2.3803811073303223
2.3796465396881104
2.3789169788360596
2.3781938552856445
2.377476215362549
2.3767645359039307
2.3760581016540527
2.375356912612915
2.374661684036255
2.3739712238311768
2.373286485671997
2.3726067543029785
2.3719322681427
2.371263027191162
2.370598554611206
2.369939088821411
2.3692846298217773
2.3686351776123047
2.367990493774414
2.3673503398895264
2.3667149543762207
2.366084098815918
2.3654582500457764
2.3648364543914795
2.3642194271087646
2.3636064529418945
2.3629980087280273
2.362394332885742
2.3617944717407227
2.361199140548706
2.360607624053955
2.360020399093628
2.3594372272491455
2.358858108520508
2.358283281326294
2.3577120304107666
2.357144832611084
2.356581687927246
2.356022357940674
2.355466365814209
2.354914665222168
2.3543665409088135
2.3538217544555664
2.353281021118164
2.352743625640869
2.35221004486084
2.351679563522339
2.3511531352996826
2.3506295680999756
2.3501102924346924
2.3495936393737793
2.3490805625915527
2.3485705852508545
2.3

In [208]:
print(probs[torch.arange(5), ys[:5]]) # overfitting for one sample: emma

tensor([0.0477, 0.1753, 0.0451, 0.1309, 0.0572], grad_fn=<IndexBackward0>)


In [219]:
# Sample from the 'neural net' model
g = torch.Generator().manual_seed(2147483647 + 4)

for i in range(5): 
    out = []
    ix = 0
    while True:
        xenc = F.one_hot(torch.tensor([ix]), num_classes=729).float()
        logits = xenc @ W
        counts = logits.exp()
        p = counts / counts.sum(dim=1, keepdim=True)

        old_comb = itoc[ix]
        ix_ch = torch.multinomial(p, num_samples=1, replacement=True, generator=g).item()
        ch = itos[ix_ch]
        comb = old_comb[1] + ch
        ix = ctoi[comb]

        out.append(itoc[ix][1])
        if itoc[ix][1] == '.':
            break
    print(''.join(out))

gara.
pyricwtt.
nia.
nyash.
leisallan.


In [ ]:
# Did the model improve over a bigram model?
# Bigram:  2.45
# Trigram: 2.32

# The loss improved about 0.2 